In [1]:
import torch
import torch.nn as nn
import numpy as np

In [2]:
from fastai.text.all import *

In [3]:
path = untar_data(URLs.IMDB)

In [4]:
if torch.cuda.is_available():
  device = "cuda:0"
else:
  device = "cpu"
device

'cpu'

In [5]:
get_imdb = partial(get_text_files,folders=['train','test','unsup'])

dls_lm = DataBlock(
    blocks=TextBlock.from_folder(path, is_lm=True),
    get_items=get_imdb, splitter=RandomSplitter(0.1)
).dataloaders(path, path=path, bs=8, seq_len=40)

In [18]:
len(dls_lm.vocab)

60008

In [6]:
dls_lm.vocab[0:10]

['xxunk',
 'xxpad',
 'xxbos',
 'xxeos',
 'xxfld',
 'xxrep',
 'xxwrep',
 'xxup',
 'xxmaj',
 'the']

In [13]:
print(dls_lm)

In [31]:
dls_lm.show_batch()

In [34]:
def scaled_dot_product_attention(query, key, value, mask=None):
    dim_k = query.size(-1)
    print("query: ",query.shape)
    scores = torch.bmm(query, key.transpose(1, 2)) / np.sqrt(dim_k)
    if mask is not None:
        scores = scores.masked_fill(mask == 0, float("-inf"))
    weights = F.softmax(scores, dim=-1)
    print("scores: ",scores.shape)
    print("weights: ",weights.shape)
    print("value: ",value.shape)
    return weights.bmm(value)

"""def scaled_dot_product_attention(query, key, value):
    dim_k = query.size(-1)
    scores = torch.bmm(query, key.transpose(1, 2)) / np.sqrt(dim_k)
    #print("scores: ",scores)
    weights = F.softmax(scores, dim=-1)
    #print("weights: ",weights)
    return torch.bmm(weights, value)"""

class AttentionHead(nn.Module):
    def __init__(self, embed_dim, head_dim, vocab_size):
        super().__init__()
        self.q = nn.Linear(embed_dim, head_dim)
        self.k = nn.Linear(embed_dim, head_dim)
        self.v = nn.Linear(embed_dim, head_dim)
        seq_len = vocab_size #inputs.input_ids.size(-1)
        self.mask = torch.tril(torch.ones(seq_len, seq_len)).unsqueeze(0)

    def forward(self, hidden_state):
        attn_outputs = scaled_dot_product_attention(
            self.q(hidden_state), self.k(hidden_state), self.v(hidden_state), self.mask)
        return attn_outputs
    
class MultiHeadAttention(nn.Module):
    def __init__(self, vocab_size, embed_dim, num_heads):
        super().__init__()
        embed_dim = embed_dim
        num_heads = num_heads
        head_dim = embed_dim // num_heads
        self.embedding = nn.Embedding(vocab_size, embed_dim)
        self.heads = nn.ModuleList(
            [AttentionHead(embed_dim, head_dim, vocab_size) for _ in range(num_heads)]
        )
        self.output_linear = nn.Linear(embed_dim, vocab_size)

    def forward(self, hidden_state):
        print(hidden_state)
        embed_state = self.embedding(hidden_state)
        print(embed_state)
        x = torch.cat([h(embed_state) for h in self.heads], dim=-1)
        x = self.output_linear(x)
        print(x)
        return x

In [ ]:
model = MultiHeadAttention(
    vocab_size=len(dls_lm.vocab), 
    embed_dim=256, 
    num_heads=4
)

learn = Learner(
    dls_lm, 
    model, 
    loss_func=CrossEntropyLossFlat(), 
    metrics=[accuracy]
)

#learn.fit_one_cycle(1, 1e-3)

tensor([[   2,    8,    9,  ...,  885,   19,  123],
        [  17,   45, 6016,  ...,   52,   97,   28],
        [ 233,   11,   12,  ..., 2098,   30,   37],
        ...,
        [ 344,  135,   40,  ...,   50,  380,    9],
        [ 292,   29, 1464,  ...,   12,    9,   32],
        [ 310,   18,    9,  ...,   54,    8,    9]])
tensor([[[-2.3842e-02, -4.4038e-01, -5.2400e-01,  ...,  1.3004e-01,
          -5.2867e-01, -1.4726e+00],
         [ 8.6131e-01,  7.1645e-01, -2.9154e-01,  ...,  1.2290e+00,
          -1.6125e-01,  4.6239e-01],
         [-6.2474e-01,  9.4308e-01, -5.0225e-02,  ..., -9.9051e-02,
           4.0932e-01,  6.2861e-01],
         ...,
         [-1.6097e-02, -5.9038e-01, -1.0003e+00,  ...,  9.2495e-01,
           4.2873e-01, -1.3621e+00],
         [-1.0967e-01,  2.8407e+00, -2.8575e-01,  ..., -2.8974e-01,
          -2.2555e-01, -5.2966e-01],
         [-1.1939e+00, -5.1316e-01, -1.0575e-01,  ...,  1.0344e+00,
          -7.6078e-01,  4.3065e-01]],

        [[-1.1491e+00, -6.11

tensor([[[ 0.0295, -0.0076,  0.0103,  ..., -0.0010,  0.0330,  0.0865],
         [ 0.0161, -0.0514, -0.0680,  ..., -0.0517,  0.0207,  0.0674],
         [ 0.0090, -0.0478, -0.0252,  ...,  0.0097,  0.0379,  0.1335],
         ...,
         [ 0.0343, -0.0039, -0.0379,  ...,  0.0083,  0.0565,  0.1023],
         [ 0.0434, -0.0173, -0.0628,  ..., -0.0169,  0.0294,  0.0315],
         [ 0.0026, -0.0257, -0.0099,  ...,  0.0005,  0.0213,  0.0885]],

        [[-0.0452, -0.0057,  0.0563,  ...,  0.0373, -0.0549,  0.0971],
         [-0.0041, -0.0165,  0.0274,  ...,  0.1002, -0.0598,  0.1411],
         [-0.0436, -0.0310,  0.0593,  ...,  0.0421, -0.0494,  0.1131],
         ...,
         [ 0.0032, -0.0055,  0.0518,  ...,  0.0680, -0.0824,  0.1112],
         [-0.0504, -0.0258,  0.0561,  ...,  0.0147, -0.0477,  0.1129],
         [-0.0134, -0.0263,  0.0488,  ...,  0.0332, -0.0564,  0.1162]],

        [[ 0.0680,  0.0355, -0.0543,  ...,  0.0191, -0.0379,  0.0611],
         [ 0.0221,  0.0275, -0.0669,  ...,  0

In [38]:
model = MultiHeadAttention(
    vocab_size=4, 
    embed_dim=5, 
    num_heads=1
)

In [39]:
toks = torch.tensor([[0,2],[1,2]])
attention = model(toks)

tensor([[0, 2],
        [1, 2]])
tensor([[[-1.6849, -0.0696, -0.2327, -0.6835,  2.0915],
         [ 0.6805, -0.4802, -0.2574, -0.6285, -1.0330]],

        [[ 1.9390,  0.9164,  0.7488, -0.8519,  0.2946],
         [ 0.6805, -0.4802, -0.2574, -0.6285, -1.0330]]],
       grad_fn=<EmbeddingBackward0>)
query:  torch.Size([2, 2, 5])


RuntimeError: The size of tensor a (4) must match the size of tensor b (2) at non-singleton dimension 2

In [61]:
attention[0]

tensor([[ 0.1084, -0.4915]], grad_fn=<SelectBackward0>)

In [26]:
import torch
import torch.nn as nn

# Example input and target tensors
input = torch.randn(3, 5)  # Input tensor with shape (batch_size, num_classes)
target = torch.tensor([1, 0, 4])  # Target tensor with shape (batch_size)

# Create an instance of CrossEntropyLoss
loss_fn = nn.CrossEntropyLoss()

# Compute the cross-entropy loss
loss = loss_fn(input, target)

print(loss)


tensor(2.6823)


In [6]:
def scaled_dot_product_attention(query, key, value, mask=None):
    dim_k = query.size(-1)
    scores = torch.bmm(query, key.transpose(1, 2)) / np.sqrt(dim_k)
    if mask is not None:
        scores = scores.masked_fill(mask == 0, float("-inf"))
    weights = F.softmax(scores, dim=-1)
    return weights.bmm(value)

class AttentionHead(nn.Module):
    def __init__(self, embed_dim, head_dim, vocab_size):
        super().__init__()
        self.q = nn.Linear(embed_dim, head_dim)
        self.k = nn.Linear(embed_dim, head_dim)
        self.v = nn.Linear(embed_dim, head_dim)
        self.mask = torch.tril(torch.ones(vocab_size, vocab_size)).unsqueeze(0)

    def forward(self, hidden_state):
        attn_outputs = scaled_dot_product_attention(
            self.q(hidden_state), self.k(hidden_state), self.v(hidden_state), self.mask)
        return attn_outputs

class MultiHeadAttention(nn.Module):
    def __init__(self, config):
        super().__init__()
        embed_dim = config.hidden_size
        num_heads = config.num_attention_heads
        head_dim = embed_dim // num_heads
        self.heads = nn.ModuleList(
            [AttentionHead(embed_dim, head_dim, 40) for _ in range(num_heads)]
        )
        self.output_linear = nn.Linear(embed_dim, embed_dim)

    def forward(self, hidden_state):
        x = torch.cat([h(hidden_state) for h in self.heads], dim=-1)
        x = self.output_linear(x)
        return x

class FeedForward(nn.Module):
    def __init__(self, config):
        super().__init__()
        self.linear_1 = nn.Linear(config.hidden_size, config.intermediate_size)
        self.linear_2 = nn.Linear(config.intermediate_size, config.hidden_size)
        self.gelu = nn.GELU()
        self.dropout = nn.Dropout(config.hidden_dropout_prob)
        
    def forward(self, x):
        x = self.linear_1(x)
        x = self.gelu(x)
        x = self.linear_2(x)
        x = self.dropout(x)
        return x

class TransformerEncoderLayer(nn.Module):
    def __init__(self, config):
        super().__init__()
        self.layer_norm_1 = nn.LayerNorm(config.hidden_size)
        self.layer_norm_2 = nn.LayerNorm(config.hidden_size)
        self.attention = MultiHeadAttention(config)
        self.feed_forward = FeedForward(config)

    def forward(self, x):
        # Apply layer normalization and then copy input into query, key, value
        hidden_state = self.layer_norm_1(x)
        # Apply attention with a skip connection
        x = x + self.attention(hidden_state)
        # Apply feed-forward layer with a skip connection
        x = x + self.feed_forward(self.layer_norm_2(x))
        return x

class Embeddings(nn.Module):
    def __init__(self, config):
        super().__init__()
        self.token_embeddings = nn.Embedding(config.vocab_size, 
                                             config.hidden_size)
        self.position_embeddings = nn.Embedding(config.max_position_embeddings,
                                                config.hidden_size)
        self.layer_norm = nn.LayerNorm(config.hidden_size, eps=1e-12)
        self.dropout = nn.Dropout()

    def forward(self, input_ids):
        # Create position IDs for input sequence
        seq_length = input_ids.size(1)
        position_ids = torch.arange(seq_length, dtype=torch.long).unsqueeze(0)
        # Create token and position embeddings
        token_embeddings = self.token_embeddings(input_ids)
        
        position_embeddings = self.position_embeddings(position_ids)
        # Combine token and position embeddings
        embeddings = token_embeddings + position_embeddings
        embeddings = self.layer_norm(embeddings)
        embeddings = self.dropout(embeddings)
        return embeddings

class TransformerEncoder(nn.Module):
    def __init__(self, config):
        super().__init__()
        self.embeddings = Embeddings(config)
        self.layers = nn.ModuleList([TransformerEncoderLayer(config) 
                                     for _ in range(config.num_hidden_layers)])

    def forward(self, x):
        x = self.embeddings(x)
        for layer in self.layers:
            x = layer(x)
        return x

class TransformerForSequenceClassification(nn.Module):
    def __init__(self, config):
        super().__init__()
        self.encoder = TransformerEncoder(config)
        self.dropout = nn.Dropout(config.hidden_dropout_prob)
        self.classifier = nn.Linear(config.hidden_size, config.num_labels)
        
    def forward(self, x):
        #print(x)
        x = self.encoder(x)#[:, 0, :] # select hidden state of [CLS] token
        #print(x)
        x = self.dropout(x)
        x = self.classifier(x)
        #print(x)
        return x

In [7]:
from transformers import AutoConfig
config = AutoConfig.from_pretrained('bert-base-uncased')

In [8]:
config.vocab_size = len(dls_lm.vocab)
config.num_labels = len(dls_lm.vocab)
config.hidden_size = 132
encoder_classifier = TransformerForSequenceClassification(config)

In [11]:
model = encoder_classifier

model.to(device)

dls_lm.to(device)

learn = Learner(
    dls_lm, 
    model, 
    loss_func=CrossEntropyLossFlat(), 
    metrics=[accuracy]
)


learn.fit_one_cycle(1, 1e-3)

learn.export('mymodel.pkl')

KeyboardInterrupt: 

In [9]:
model = encoder_classifier

learn = Learner(
    dls_lm, 
    model, 
    loss_func=CrossEntropyLossFlat(), 
    metrics=[accuracy]
)

learn.fit_one_cycle(1, 1e-3)

learn.export('mymodel.pkl')

KeyboardInterrupt: 

In [9]:
config

BertConfig {
  "_name_or_path": "bert-base-uncased",
  "architectures": [
    "BertForMaskedLM"
  ],
  "attention_probs_dropout_prob": 0.1,
  "classifier_dropout": null,
  "gradient_checkpointing": false,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.1,
  "hidden_size": 768,
  "id2label": {
    "0": "LABEL_0",
    "1": "LABEL_1",
    "2": "LABEL_2",
    "3": "LABEL_3",
    "4": "LABEL_4",
    "5": "LABEL_5",
    "6": "LABEL_6",
    "7": "LABEL_7",
    "8": "LABEL_8",
    "9": "LABEL_9",
    "10": "LABEL_10",
    "11": "LABEL_11",
    "12": "LABEL_12",
    "13": "LABEL_13",
    "14": "LABEL_14",
    "15": "LABEL_15",
    "16": "LABEL_16",
    "17": "LABEL_17",
    "18": "LABEL_18",
    "19": "LABEL_19",
    "20": "LABEL_20",
    "21": "LABEL_21",
    "22": "LABEL_22",
    "23": "LABEL_23",
    "24": "LABEL_24",
    "25": "LABEL_25",
    "26": "LABEL_26",
    "27": "LABEL_27",
    "28": "LABEL_28",
    "29": "LABEL_29",
    "30": "LABEL_30",
    "31": "LABEL_31",
    "32": "LABEL_32

In [17]:
learn = Learner(
    dls_lm, 
    model, 
    loss_func=CrossEntropyLossFlat(), 
    metrics=[accuracy]
)

In [21]:
model_path = '~/Unitversity/GNN/project/my_model.pk1'

learn.export(model_path)

RuntimeError: Parent directory /home/chris/.fastai/data/imdb/~/Unitversity/GNN/project does not exist.

In [22]:
learn.export('mymodel.pkl')